<a href="https://colab.research.google.com/github/Hidetsune/SemEval2024_Task3_Hidetsune/blob/main/SemEval_2024_Task_3_main_solutions_Hidetsune_Takahashi_.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#SemEval2024 Task3 Hidetsune Takahashi

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import pandas as pd
import json

In [ ]:
import re

In [ ]:
import spacy
!python -m spacy download en_core_web_lg
nlp = spacy.load("en_core_web_lg")


2024-01-17 01:28:47.298344: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-01-17 01:28:47.298422: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-01-17 01:28:47.299909: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-01-17 01:28:48.451076: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 587.7/587.7 MB 1.7 MB/s eta 0:00:00
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_lg')


#Datasets
datasets (dataset_text_emotion_train, dataset_text_emotion_validation, dataset_text_emotion_evaluation)

[Reference](https://heartbeat.comet.ml/emotion-classification-with-spacy-v3-comet-eaff310c0d7c)

In [ ]:
!pip install "spacy >= 3.0.6"
!pip install "comet_ml>=3.31.19"
!pip install datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 589.9/589.9 kB 3.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 25.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.5/54.5 kB 3.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 254.1/254.1 kB 19.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 137.9/137.9 kB 14.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.3/54.3 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 514.7/514.7 kB 6.4 MB/s eta 0:00:00
  Attempting uninstall: websocket-client
    Found existing installation: websocket-client 1.7.0
    Uninstalling websocket-client-1.7.0:
      Successfully uninstalled websocket-client-1.7.0
  Attempting uninstall: python-box
    Found existing installation: python-box 7.1.1
    Uninstalling python-box-7.1.1:
      Successfully uninstalled python-box-7.1.1
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 507.1/507.1 kB 5.0 MB/s e

In [ ]:
%env COMET_API_KEY=<"zKfFM345o2F1kk8KGHtVJy7kO">
%env COMET_PROJECT_NAME=<"semeval2024-Task3">

env: COMET_API_KEY=<"zKfFM345o2F1kk8KGHtVJy7kO">
env: COMET_PROJECT_NAME=<"semeval2024-Task3">


In [ ]:
text_emotion_pair = pd.read_csv("/content/drive/MyDrive/SemEval Task3/emotion_data_ver1_with F1 score of app.0.18.csv") #CHANGE HERE
text_emotion_pair

text  emotion
0      Alright , so I am back in high school , I am s...  neutral
1                           Oh , yeah . Had that dream .  neutral
2                                 Never had that dream .  neutral
3                                                   No .  neutral
4           All of a sudden , the phone starts to ring .  neutral
...                                                  ...      ...
33398                  Cmon people match think Dick Togo     fear
33399                              Cant wait till factor     fear
33400                                    walk faith live     fear
33401  waste day busyMake sure productive things want...     fear
33402  ads insurance  Sherwood s draw attention anxio...     fear

[33403 rows x 2 columns]

In [ ]:
categories = ["neutral", "surprise", "anger", "sadness", "joy", "disgust", "fear"]

In [ ]:
labels_ = {"neutral":0, "surprise":1,  "anger":2,  "sadness":3, "joy":4, "disgust":5, "fear":6}

In [ ]:
from sklearn.model_selection import train_test_split

In [ ]:
text_emotion_pair_train, text_emotion_pair_validation_evaluation = train_test_split(text_emotion_pair, test_size=0.001, random_state=10)
text_emotion_pair_validation, text_emotion_pair_evaluation = train_test_split(text_emotion_pair_validation_evaluation, test_size=0.001, random_state=101)

In [ ]:
from datasets import Dataset, Value, ClassLabel, Features  #added

In [ ]:
from datasets import Dataset
dataset_text_emotion_train = Dataset.from_pandas(text_emotion_pair_train)
dataset_text_emotion_validation = Dataset.from_pandas(text_emotion_pair_validation)
dataset_text_emotion_evaluation = Dataset.from_pandas(text_emotion_pair_evaluation)

In [ ]:
new_features = dataset_text_emotion_train.features.copy()

In [ ]:
new_features['text'] = Value('large_string')
new_features['emotion'] = ClassLabel(names=['neutral', 'surprise', 'anger', 'sadness', 'joy', 'disgust','fear'])

In [ ]:
dataset_text_emotion_train = dataset_text_emotion_train.cast(new_features)
dataset_text_emotion_validation = dataset_text_emotion_validation.cast(new_features)
dataset_text_emotion_evaluation = dataset_text_emotion_evaluation.cast(new_features)

Casting the dataset:   0%|          | 0/33369 [00:00<?, ? examples/s]

Casting the dataset:   0%|          | 0/33 [00:00<?, ? examples/s]

Casting the dataset:   0%|          | 0/1 [00:00<?, ? examples/s]

In [ ]:
dataset_text_emotion_train.features

{'text': Value(dtype='large_string', id=None),
 'emotion': ClassLabel(names=['neutral', 'surprise', 'anger', 'sadness', 'joy', 'disgust', 'fear'], id=None),
 '__index_level_0__': Value(dtype='int64', id=None)}

In [ ]:
dataset_text_emotion_validation.features

{'text': Value(dtype='large_string', id=None),
 'emotion': ClassLabel(names=['neutral', 'surprise', 'anger', 'sadness', 'joy', 'disgust', 'fear'], id=None),
 '__index_level_0__': Value(dtype='int64', id=None)}

In [ ]:
dataset_text_emotion_evaluation.features

{'text': Value(dtype='large_string', id=None),
 'emotion': ClassLabel(names=['neutral', 'surprise', 'anger', 'sadness', 'joy', 'disgust', 'fear'], id=None),
 '__index_level_0__': Value(dtype='int64', id=None)}

#Training
actual learning starts

In [ ]:
from typing import Set, List, Tuple
from spacy.tokens import DocBin
import spacy
from tqdm.auto import tqdm

In [ ]:
import locale
def getpreferredencoding(do_setlocale = True):
    return "UTF-8"

locale.getpreferredencoding = getpreferredencoding

In [ ]:
def convert_spacy_dataset(dataset, target_file: str, labels):
  nlp = spacy.blank("en")
  db = DocBin()

  for item in tqdm(dataset):
    doc = nlp.make_doc(item["text"])
    doc.cats = {label: 0 for label in labels}
    doc.cats[labels[item["emotion"]]] = 1

    db.add(doc)

  db.to_disk(target_file)
  return db

In [ ]:
convert_spacy_dataset(dataset_text_emotion_train, "train_data.spacy", categories)
convert_spacy_dataset(dataset_text_emotion_validation, "validation_data.spacy", categories)
convert_spacy_dataset(dataset_text_emotion_evaluation, "test_data.spacy", categories)

  0%|          | 0/33369 [00:00<?, ?it/s]

  0%|          | 0/33 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
!python -m spacy init config --lang en --pipeline textcat_multilabel comet_config.cfg  #training model

2024-01-17 01:30:39.442946: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-01-17 01:30:39.443030: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-01-17 01:30:39.444949: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-01-17 01:30:42.258984: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
⚠ To generate a more effective transformer-based config (GPU-only),
install the spacy-transformers package and re-run this command. The config
generated now does not use transformers.
ℹ Generated config template specific for your use case
- 

In [ ]:
from spacy.cli.train import train as spacy_train

config_path = "comet_config.cfg"
output_model_path = "output_models/"

spacy_train(
    config_path,
    output_path=output_model_path,
    overrides={
        "paths.train": "train_data.spacy",
        "paths.dev": "validation_data.spacy",
    },
    use_gpu=0

)


✔ Created output directory: output_models
ℹ Saving to output directory: output_models
ℹ Using GPU: 0

=========================== Initializing pipeline ===========================
✔ Initialized pipeline

============================= Training pipeline =============================
ℹ Pipeline: ['textcat_multilabel']
ℹ Initial learn rate: 0.001
E    #       LOSS TEXTC...  CATS_SCORE  SCORE 
---  ------  -------------  ----------  ------
  0       0           0.25       58.98    0.59
  0     200          36.35       63.41    0.63
  0     400          26.55       66.21    0.66
  0     600          23.82       68.25    0.68
  0     800          22.22       69.79    0.70
  0    1000          21.60       71.90    0.72
  0    1200          20.36       73.97    0.74
  0    1400          20.03       75.44    0.75
  1    1600          19.17       76.82    0.77
  1    1800          17.95       78.57    0.79
  1    2000          17.69       78.59    0.79
  2    2200          17.11       79.16    0.

#Evaluation

In [ ]:
!python -m spacy evaluate output_models/model-best/ test_data.spacy

2024-01-17 01:34:52.992722: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-01-17 01:34:52.992793: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-01-17 01:34:52.994321: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-01-17 01:34:54.289249: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
ℹ Using CPU
ℹ To switch to GPU 0, use the option: --gpu-id 0

================================== Results ==================================

TOK                   100.00
TEXTCAT (macro AUC)   0.00  
SPEED                 16174 


===========

In [ ]:
dataset_text_emotion_evaluation

Dataset({
    features: ['text', 'emotion', '__index_level_0__'],
    num_rows: 1
})

In [ ]:
text_emotion_pair_evaluation.emotion_list = list(text_emotion_pair_evaluation.emotion)
text_emotion_pair_evaluation.text_list = list(text_emotion_pair_evaluation.text)

<ipython-input-30-450349b88143>:1: UserWarning: Pandas doesn't allow columns to be created via a new attribute name - see https://pandas.pydata.org/pandas-docs/stable/indexing.html#attribute-access
  text_emotion_pair_evaluation.emotion_list = list(text_emotion_pair_evaluation.emotion)
<ipython-input-30-450349b88143>:2: UserWarning: Pandas doesn't allow columns to be created via a new attribute name - see https://pandas.pydata.org/pandas-docs/stable/indexing.html#attribute-access
  text_emotion_pair_evaluation.text_list = list(text_emotion_pair_evaluation.text)


In [ ]:
print(text_emotion_pair_evaluation.text_list[0:6])
print(text_emotion_pair_evaluation.emotion_list[0:6])

['awkward moment fat guy cockblocks away hot guy #shuttleride']
['sadness']


In [ ]:
trained_nlp = spacy.load("output_models/model-best/")


texts = text_emotion_pair_evaluation.text_list[0:6]

category_scores = [doc.cats for doc in trained_nlp.pipe(texts)]


thresh = 0.1
for d in category_scores:
  print(dict((k, v) for k, v in d.items() if v >= thresh))

{'surprise': 0.43040600419044495, 'anger': 0.18437309563159943, 'sadness': 0.23662975430488586, 'disgust': 0.6041263937950134}


#Trial
[Next Sentence Prediction Reference](https://www.scaler.com/topics/nlp/bert-next-sentence-prediction/)

In [ ]:
!pip install transformers

In [ ]:
from transformers import BertTokenizer, BertForNextSentencePrediction
import torch

In [ ]:
json_open_trial = open("/content/drive/MyDrive/SemEval Task3/Subtask_2_test.json","r")  # Subtask_2_trial.json
json_load_trial = json.load(json_open_trial)

In [ ]:
Trial_Data = json_load_trial

In [ ]:
Trial_Data

[{'conversation_ID': 1375,
  'conversation': [{'utterance_ID': 1,
    'text': 'Please do not do that again . It is a horrible sound .',
    'speaker': 'Chandler',
    'video_name': 'dia1375utt1.mp4'},
   {'utterance_ID': 2,
    'text': 'Uh , it is Paul .',
    'speaker': 'Paul',
    'video_name': 'dia1375utt2.mp4'},
   {'utterance_ID': 3,
    'text': 'Buzz him in .',
    'speaker': 'Monica',
    'video_name': 'dia1375utt3.mp4'},
   {'utterance_ID': 4,
    'text': 'Who is Paul ?',
    'speaker': 'Joey',
    'video_name': 'dia1375utt4.mp4'},
   {'utterance_ID': 5,
    'text': 'Paul , the wine guy , Paul ?',
    'speaker': 'Ross',
    'video_name': 'dia1375utt5.mp4'},
   {'utterance_ID': 6,
    'text': 'Maybe .',
    'speaker': 'Monica',
    'video_name': 'dia1375utt6.mp4'},
   {'utterance_ID': 7,
    'text': 'Wait a minute . Your " not a real date " is with Paul , the wine guy ?',
    'speaker': 'Joey',
    'video_name': 'dia1375utt7.mp4'},
   {'utterance_ID': 8,
    'text': 'He finally 

In [ ]:
for i in Trial_Data:
  i["emotion-cause_pairs"] = []


In [ ]:
Trial_Data

[{'conversation_ID': 1375,
  'conversation': [{'utterance_ID': 1,
    'text': 'Please do not do that again . It is a horrible sound .',
    'speaker': 'Chandler',
    'video_name': 'dia1375utt1.mp4'},
   {'utterance_ID': 2,
    'text': 'Uh , it is Paul .',
    'speaker': 'Paul',
    'video_name': 'dia1375utt2.mp4'},
   {'utterance_ID': 3,
    'text': 'Buzz him in .',
    'speaker': 'Monica',
    'video_name': 'dia1375utt3.mp4'},
   {'utterance_ID': 4,
    'text': 'Who is Paul ?',
    'speaker': 'Joey',
    'video_name': 'dia1375utt4.mp4'},
   {'utterance_ID': 5,
    'text': 'Paul , the wine guy , Paul ?',
    'speaker': 'Ross',
    'video_name': 'dia1375utt5.mp4'},
   {'utterance_ID': 6,
    'text': 'Maybe .',
    'speaker': 'Monica',
    'video_name': 'dia1375utt6.mp4'},
   {'utterance_ID': 7,
    'text': 'Wait a minute . Your " not a real date " is with Paul , the wine guy ?',
    'speaker': 'Joey',
    'video_name': 'dia1375utt7.mp4'},
   {'utterance_ID': 8,
    'text': 'He finally 

In [ ]:
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertForNextSentencePrediction.from_pretrained('bert-base-uncased')

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/28.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

In [ ]:
def bert_next_sentence(sent1,sent2):
  tokenized = tokenizer(sent1, sent2, return_tensors='pt')
  labels = torch.LongTensor([0])
  predict = model(**tokenized, labels=labels)
  prediction = torch.argmax(predict.logits)
  if prediction == 0:
    return True
  else:
    return False

In [ ]:
for i in Trial_Data:
  ID_text_listy = []
  for conv in i["conversation"]:
    local_list = []
    ID_listy = []
    #print(conv)
    #ID_text_listy = []
    #print(utterance)
    #print(utterance[text])
    ID_text_listy.append([conv["utterance_ID"], conv["text"]])
    d = trained_nlp(conv["text"]).cats
    emotion = max(d, key =d.get )
    if emotion == "neutral":
      pass
    else:
      #local_list = []
      local_list.append(f'{conv["utterance_ID"]}_{emotion}')
      #print(ID_text_listy)

      for j in ID_text_listy:
        if bert_next_sentence(j[1],conv["text"]):
          #print(j[0])
          ID_listy.append(str(j[0]))
      try:
        local_list.append(ID_listy[-2])
      except IndexError:
        local_list.append(ID_listy[-1])
      i["emotion-cause_pairs"].append(local_list)
      local_list = []
      ID_listy = []

  #if len(local_list) == 1:
    #local_list.append(ID_text_listy[-1][0])
  #elif len(local_list) == 2:
    #continue
  #else:
    #print("error")
    #print(local_list)
    #i["emotion-cause_pairs"].append(local_list)
    #local_list = []
    #print(local_list)



In [ ]:
Trial_Data

[{'conversation_ID': 1375,
  'conversation': [{'utterance_ID': 1,
    'text': 'Please do not do that again . It is a horrible sound .',
    'speaker': 'Chandler',
    'video_name': 'dia1375utt1.mp4'},
   {'utterance_ID': 2,
    'text': 'Uh , it is Paul .',
    'speaker': 'Paul',
    'video_name': 'dia1375utt2.mp4'},
   {'utterance_ID': 3,
    'text': 'Buzz him in .',
    'speaker': 'Monica',
    'video_name': 'dia1375utt3.mp4'},
   {'utterance_ID': 4,
    'text': 'Who is Paul ?',
    'speaker': 'Joey',
    'video_name': 'dia1375utt4.mp4'},
   {'utterance_ID': 5,
    'text': 'Paul , the wine guy , Paul ?',
    'speaker': 'Ross',
    'video_name': 'dia1375utt5.mp4'},
   {'utterance_ID': 6,
    'text': 'Maybe .',
    'speaker': 'Monica',
    'video_name': 'dia1375utt6.mp4'},
   {'utterance_ID': 7,
    'text': 'Wait a minute . Your " not a real date " is with Paul , the wine guy ?',
    'speaker': 'Joey',
    'video_name': 'dia1375utt7.mp4'},
   {'utterance_ID': 8,
    'text': 'He finally 

#Submition Format
"Subtask_2_pred.zip"

inside the zip fine, "Subtask_2_pred.json"

In [ ]:
import json

In [ ]:
dir = "Task3_Subtask_2b_pred.json"
data = Trial_Data

In [ ]:
with open(dir, mode="wt", encoding = "utf-8") as f:
  json.dump(data,f,ensure_ascii=False, indent=4)

In [ ]:
#data